# Домашнее задание  № 5. Матричные разложения/Тематическое моделирование

In [1]:
import warnings
warnings.filterwarnings("ignore")

In [76]:
import gensim
import pandas as pd
import numpy as np
from pymorphy3 import MorphAnalyzer
from collections import Counter
from string import punctuation
from razdel import tokenize as razdel_tokenize
from IPython.display import Image
from IPython.core.display import HTML 
from sklearn.decomposition import TruncatedSVD, NMF, PCA, LatentDirichletAllocation
from sklearn.manifold import TSNE
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer, TfidfTransformer
from sklearn.metrics.pairwise import cosine_distances
from sklearn.ensemble import RandomForestClassifier, ExtraTreesClassifier
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix
from sklearn.pipeline import Pipeline
from sklearn.model_selection import KFold, StratifiedKFold
import pyLDAvis.gensim_models


In [52]:
from sklearn.linear_model import SGDClassifier

In [66]:
from sklearn.neighbors import KNeighborsClassifier

In [3]:
morph = MorphAnalyzer()

### Задание № 1 (8 баллов)

Попробуйте матричные разложения с 4 классификаторами - SGDClassifier, KNeighborsClassifier,  RandomForest, ExtraTreesClassifier (про него подробнее почитайте в документации, он похож на RF). Используйте и NMF, SVD и LDA. Сравните результаты на кросс-валидации и выберите лучшее сочетание.

В итоге у вас должно получиться, как минимум 12 моделей (три разложения на каждый классификатор). Используйте 1 и те же параметры кросс-валидации. Параметры векторизации, параметры K в матричных разложениях, параметры классификаторов могут быть разными между экспериментами.

Можете взять поменьше данных, если все будет обучаться слишком долго (не ставьте параметр K слишком большим в NMF и LDA, иначе точно будет слишком долго)

In [4]:
# добавим лемматизацию
def normalize(text):
    normalized_text = [word.text.strip(punctuation) for word \
                                                            in razdel_tokenize(text)]
    normalized_text = [word.lower() for word in normalized_text if word and len(word) < 20 ]
    normalized_text = [morph.parse(word)[0].normal_form for word in normalized_text]
    return ' '.join(normalized_text)

In [5]:
def eval_table(X, y, pipeline, N=6):
    # зафиксируем порядок классов
    labels = list(set(y))
    
    # метрики отдельных фолдов будет хранить в табличке
    fold_metrics = pd.DataFrame(index=labels)
    # дополнительно также соберем таблицу ошибок
    errors = np.zeros((len(labels), len(labels)))
    
    # создаем стратегию кросс-валидации
    # shuffle=True (перемешивание) - часто критично важно указать
    # т.к. данные могут быть упорядочены и модель на этом обучится
    kfold = StratifiedKFold(n_splits=N, shuffle=True, )
    
    for i, (train_index, test_index) in enumerate(kfold.split(X, y)):
        # fit-predict как и раньше, но сразу пайплайном
        pipeline.fit(X[train_index], y[train_index])
        preds = pipeline.predict(X[test_index])
        
        # записываем метрику и индекс фолда
        fold_metrics[f'precision_{i}'] = precision_score(y[test_index], preds, labels=labels, average=None)
        fold_metrics[f'recall_{i}'] = recall_score(y[test_index], preds, labels=labels, average=None)
        fold_metrics[f'f1_{i}'] = f1_score(y[test_index], preds, labels=labels, average=None)
        errors += confusion_matrix(y[test_index], preds, labels=labels, normalize='true')
    
    # таблица для усредненных значений
    # тут мы берем колонки со значениями и усредняем их
    # часто также все метрики сразу суммируют и в конце просто делят на количество фолдов
    # но мы тут помимо среднего также хотим посмотреть на стандартное отклонение
    # чтобы понять как сильно варьируются оценки моделей
    result = pd.DataFrame(index=labels)
    result['precision'] = fold_metrics[[f'precision_{i}' for i in range(N)]].mean(axis=1).round(2)
    result['precision_std'] = fold_metrics[[f'precision_{i}' for i in range(N)]].std(axis=1).round(2)
    
    result['recall'] = fold_metrics[[f'recall_{i}' for i in range(N)]].mean(axis=1).round(2)
    result['recall_std'] = fold_metrics[[f'recall_{i}' for i in range(N)]].std(axis=1).round(2)
    
    result['f1'] = fold_metrics[[f'f1_{i}' for i in range(N)]].mean(axis=1).round(2)
    result['f1_std'] = fold_metrics[[f'f1_{i}' for i in range(N)]].std(axis=1).round(2)
    
    # добавим одну колонку со средним по всем классам
    result.loc['mean'] = result.mean().round(2)
    # проценты ошибок просто усредняем
    errors /= N
    
    return result, errors

In [47]:
data = pd.read_csv('avito_category_classification.csv')

In [48]:
data['description_norm'] = data['description'].apply(normalize)

In [8]:
data

category_name  \
0                     Автомобили   
1         Детская одежда и обувь   
2              Предложение услуг   
3                     Автомобили   
4                Бытовая техника   
...                          ...   
9893  Товары для детей и игрушки   
9894      Детская одежда и обувь   
9895   Одежда, обувь, аксессуары   
9896      Детская одежда и обувь   
9897             Бытовая техника   

                                            description  \
0               отличное состояние,обслужиание в салоне   
1     В отличном состоянии. Фирма KIKO. Очень теплый...   
2     Изготовление ограждений, перил,качелей, турник...   
3     Автомобиль в отличном техническом состоянии. О...   
4     Продается газовая плита "Гефест" (Белоруссия) ...   
...                                                 ...   
9893  Чтобы посмотреть весь ассортимент нашего магаз...   
9894  Весна,осень.74-80.вопросы можно в вайбер,двухс...   
9895  Кимоно Green Hill. Состояние  отличное,  рост ...   
9896  Б/у кроссовки на девочку. Носили только в спор...   
9897                            Холодильник на гарантии   

                                       description_norm  
0                отличный состояние обслужиание в салон  
1     в отличный состояние фирма kiko очень тёплый у...  
2     изготовление ограждение перила качели турников...  
3     автомобиль в отличный технический состояние од...  
4     продаваться газовый плита гефест белоруссия б ...  
...                                                 ...  
9893  чтобы посмотреть весь ассортимент наш магазин ...  
9894  весна осень 74-80 вопрос можно в вайбер двухст...  
9895  кимоно green hill состояние отличный рост 160-...  
9896  б у кроссовок на девочка носить только в спортзал  
9897                            холодильник на гарантия  

[9898 rows x 3 columns]

_________________________________________________________________________________________________________________________________________________

## SVD + RandomForest

In [11]:
pipeline_svd_rf = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=5, max_df=0.4)),
    ('svd', TruncatedSVD(250)),
    ('clf', RandomForestClassifier(n_estimators=100, max_depth=10))
])

In [14]:
metrics_svd_rf, errors_svd_rf = eval_table(data['description_norm'], data['category_name'], pipeline_svd_rf)

In [15]:
metrics_svd_rf

precision  precision_std  recall  recall_std  \
Мебель и интерьер                0.82           0.15    0.05        0.02   
Квартиры                         0.90           0.01    0.89        0.03   
Предложение услуг                0.68           0.03    0.59        0.06   
Одежда, обувь, аксессуары        0.47           0.02    0.75        0.03   
Телефоны                         0.92           0.02    0.39        0.06   
Детская одежда и обувь           0.47           0.01    0.68        0.02   
Товары для детей и игрушки       0.80           0.07    0.22        0.04   
Автомобили                       0.83           0.06    0.63        0.05   
Ремонт и строительство           0.73           0.09    0.12        0.03   
Бытовая техника                  0.86           0.16    0.06        0.02   
mean                             0.75           0.06    0.44        0.04   

                              f1  f1_std  
Мебель и интерьер           0.09    0.04  
Квартиры                    0.89    0.02  
Предложение услуг           0.63    0.04  
Одежда, обувь, аксессуары   0.58    0.02  
Телефоны                    0.55    0.06  
Детская одежда и обувь      0.56    0.01  
Товары для детей и игрушки  0.34    0.05  
Автомобили                  0.72    0.04  
Ремонт и строительство      0.20    0.04  
Бытовая техника             0.12    0.04  
mean                        0.47    0.04

## NMF + RandomForest

In [16]:
pipeline_nmf_rf = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('clf', RandomForestClassifier(n_estimators=200, max_depth=6))
])

In [18]:
metrics_nmf_rf, errors_nmf_rf = eval_table(data['description_norm'], data['category_name'], pipeline_nmf_rf)

In [90]:
metrics_nmf_rf

precision  precision_std  recall  recall_std  \
Мебель и интерьер                0.81           0.11    0.12        0.08   
Квартиры                         0.84           0.04    0.96        0.02   
Предложение услуг                0.70           0.04    0.47        0.07   
Одежда, обувь, аксессуары        0.46           0.05    0.81        0.06   
Телефоны                         0.94           0.06    0.35        0.08   
Детская одежда и обувь           0.61           0.08    0.70        0.06   
Товары для детей и игрушки       0.85           0.04    0.38        0.07   
Автомобили                       0.88           0.03    0.77        0.02   
Ремонт и строительство           0.75           0.18    0.06        0.03   
Бытовая техника                  0.67           0.52    0.03        0.03   
mean                             0.75           0.12    0.46        0.05   

                              f1  f1_std  
Мебель и интерьер           0.19    0.11  
Квартиры                    0.90    0.03  
Предложение услуг           0.55    0.04  
Одежда, обувь, аксессуары   0.59    0.02  
Телефоны                    0.50    0.08  
Детская одежда и обувь      0.65    0.03  
Товары для детей и игрушки  0.52    0.07  
Автомобили                  0.82    0.02  
Ремонт и строительство      0.11    0.05  
Бытовая техника             0.06    0.06  
mean                        0.49    0.05

## LDA + RandomForest

In [49]:
pipeline_lda_rf = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', LatentDirichletAllocation(50)),
    ('clf', RandomForestClassifier(n_estimators=200, max_depth=6))
])

In [50]:
metrics_lda_rf, errors_lda_rf = eval_table(data['description_norm'], data['category_name'], pipeline_lda_rf)

In [51]:
metrics_lda_rf

precision  precision_std  recall  recall_std  \
Мебель и интерьер                0.10           0.24    0.01        0.01   
Квартиры                         0.76           0.06    0.92        0.03   
Предложение услуг                0.51           0.05    0.24        0.11   
Одежда, обувь, аксессуары        0.39           0.02    0.63        0.07   
Телефоны                         0.70           0.08    0.49        0.11   
Детская одежда и обувь           0.49           0.09    0.60        0.04   
Товары для детей и игрушки       0.60           0.15    0.27        0.08   
Автомобили                       0.66           0.12    0.67        0.12   
Ремонт и строительство           0.46           0.20    0.06        0.04   
Бытовая техника                  0.00           0.00    0.00        0.00   
mean                             0.47           0.10    0.39        0.06   

                              f1  f1_std  
Мебель и интерьер           0.01    0.02  
Квартиры                    0.83    0.04  
Предложение услуг           0.31    0.11  
Одежда, обувь, аксессуары   0.48    0.03  
Телефоны                    0.57    0.08  
Детская одежда и обувь      0.54    0.06  
Товары для детей и игрушки  0.36    0.08  
Автомобили                  0.66    0.10  
Ремонт и строительство      0.10    0.07  
Бытовая техника             0.00    0.00  
mean                        0.39    0.06

_________________________________________________________________________________________________________________________________________________

## SVD + SGDClassifier

In [55]:
pipeline_svd_sgd = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=5, max_df=0.4)),
    ('svd', TruncatedSVD(250)),
    ('clf', SGDClassifier(tol=1e-3))
])

In [56]:
metrics_svd_sgd, errors_svd_sgd = eval_table(data['description_norm'], data['category_name'], pipeline_svd_sgd)

In [57]:
metrics_svd_sgd

precision  precision_std  recall  recall_std  \
Мебель и интерьер                0.64           0.06    0.61        0.07   
Квартиры                         0.95           0.02    0.96        0.02   
Предложение услуг                0.75           0.06    0.75        0.04   
Одежда, обувь, аксессуары        0.68           0.06    0.75        0.07   
Телефоны                         0.82           0.09    0.79        0.06   
Детская одежда и обувь           0.72           0.06    0.75        0.07   
Товары для детей и игрушки       0.77           0.07    0.60        0.05   
Автомобили                       0.87           0.03    0.88        0.05   
Ремонт и строительство           0.58           0.05    0.47        0.09   
Бытовая техника                  0.68           0.07    0.47        0.04   
mean                             0.75           0.06    0.70        0.06   

                              f1  f1_std  
Мебель и интерьер           0.62    0.03  
Квартиры                    0.95    0.01  
Предложение услуг           0.75    0.04  
Одежда, обувь, аксессуары   0.71    0.02  
Телефоны                    0.80    0.02  
Детская одежда и обувь      0.73    0.02  
Товары для детей и игрушки  0.67    0.03  
Автомобили                  0.88    0.01  
Ремонт и строительство      0.51    0.07  
Бытовая техника             0.55    0.02  
mean                        0.72    0.03

## NMF + SGDClassifier

In [60]:
pipeline_nmf_sgd = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('clf', SGDClassifier(tol=1e-3))
])

In [61]:
metrics_nmf_sgd, errors_nmf_sgd = eval_table(data['description_norm'], data['category_name'], pipeline_nmf_sgd)

In [62]:
metrics_nmf_sgd

precision  precision_std  recall  recall_std  \
Мебель и интерьер                0.66           0.18    0.34        0.07   
Квартиры                         0.77           0.17    0.94        0.05   
Предложение услуг                0.72           0.15    0.34        0.16   
Одежда, обувь, аксессуары        0.61           0.09    0.71        0.11   
Телефоны                         0.69           0.20    0.53        0.21   
Детская одежда и обувь           0.62           0.10    0.66        0.14   
Товары для детей и игрушки       0.70           0.22    0.39        0.12   
Автомобили                       0.62           0.27    0.72        0.22   
Ремонт и строительство           0.15           0.17    0.15        0.20   
Бытовая техника                  0.63           0.23    0.09        0.07   
mean                             0.62           0.18    0.49        0.14   

                              f1  f1_std  
Мебель и интерьер           0.43    0.02  
Квартиры                    0.83    0.10  
Предложение услуг           0.42    0.14  
Одежда, обувь, аксессуары   0.64    0.03  
Телефоны                    0.54    0.08  
Детская одежда и обувь      0.62    0.05  
Товары для детей и игрушки  0.46    0.08  
Автомобили                  0.59    0.12  
Ремонт и строительство      0.14    0.16  
Бытовая техника             0.14    0.10  
mean                        0.48    0.09

## LDA + SGDClassifier

In [63]:
pipeline_lda_sgd = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', LatentDirichletAllocation(50)),
    ('clf', SGDClassifier(tol=1e-3))
])

In [64]:
metrics_lda_sgd, errors_lda_sgd = eval_table(data['description_norm'], data['category_name'], pipeline_lda_sgd)

In [65]:
metrics_lda_sgd

precision  precision_std  recall  recall_std  \
Мебель и интерьер                0.48           0.14    0.20        0.10   
Квартиры                         0.68           0.11    0.96        0.01   
Предложение услуг                0.47           0.14    0.45        0.09   
Одежда, обувь, аксессуары        0.53           0.05    0.61        0.07   
Телефоны                         0.55           0.13    0.63        0.07   
Детская одежда и обувь           0.58           0.04    0.56        0.08   
Товары для детей и игрушки       0.50           0.12    0.37        0.20   
Автомобили                       0.63           0.12    0.70        0.29   
Ремонт и строительство           0.16           0.14    0.09        0.14   
Бытовая техника                  0.06           0.08    0.04        0.08   
mean                             0.46           0.11    0.46        0.11   

                              f1  f1_std  
Мебель и интерьер           0.26    0.09  
Квартиры                    0.79    0.07  
Предложение услуг           0.45    0.08  
Одежда, обувь, аксессуары   0.57    0.04  
Телефоны                    0.58    0.10  
Детская одежда и обувь      0.57    0.05  
Товары для детей и игрушки  0.38    0.13  
Автомобили                  0.61    0.21  
Ремонт и строительство      0.10    0.14  
Бытовая техника             0.04    0.07  
mean                        0.43    0.10

_________________________________________________________________________________________________________________________________________________

## SVD + KNeighborsClassifier

In [67]:
pipeline_svd_kn = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=5, max_df=0.4)),
    ('svd', TruncatedSVD(250)),
    ('clf', KNeighborsClassifier(n_neighbors=10, metric='cosine'))
])

In [68]:
metrics_svd_kn, errors_svd_kn = eval_table(data['description_norm'], data['category_name'], pipeline_svd_kn)

In [69]:
metrics_svd_kn

precision  precision_std  recall  recall_std  \
Мебель и интерьер                0.43           0.07    0.27        0.05   
Квартиры                         0.92           0.03    0.88        0.02   
Предложение услуг                0.59           0.05    0.68        0.04   
Одежда, обувь, аксессуары        0.50           0.01    0.64        0.02   
Телефоны                         0.80           0.02    0.43        0.03   
Детская одежда и обувь           0.52           0.01    0.66        0.03   
Товары для детей и игрушки       0.66           0.08    0.32        0.04   
Автомобили                       0.70           0.04    0.71        0.04   
Ремонт и строительство           0.43           0.08    0.18        0.05   
Бытовая техника                  0.42           0.04    0.26        0.09   
mean                             0.60           0.04    0.50        0.04   

                              f1  f1_std  
Мебель и интерьер           0.33    0.06  
Квартиры                    0.90    0.01  
Предложение услуг           0.63    0.02  
Одежда, обувь, аксессуары   0.56    0.01  
Телефоны                    0.56    0.02  
Детская одежда и обувь      0.58    0.02  
Товары для детей и игрушки  0.43    0.05  
Автомобили                  0.70    0.03  
Ремонт и строительство      0.25    0.06  
Бытовая техника             0.32    0.07  
mean                        0.53    0.03

## NMF + KNeighborsClassifier

In [70]:
pipeline_nmf_kn = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('clf', KNeighborsClassifier(n_neighbors=10, metric='cosine'))
])

In [71]:
metrics_nmf_kn, errors_nmf_kn = eval_table(data['description_norm'], data['category_name'], pipeline_nmf_kn)

In [72]:
metrics_nmf_kn

precision  precision_std  recall  recall_std  \
Мебель и интерьер                0.40           0.03    0.29        0.07   
Квартиры                         0.84           0.04    0.80        0.08   
Предложение услуг                0.57           0.04    0.59        0.05   
Одежда, обувь, аксессуары        0.51           0.04    0.59        0.03   
Телефоны                         0.61           0.08    0.46        0.07   
Детская одежда и обувь           0.54           0.03    0.60        0.05   
Товары для детей и игрушки       0.51           0.09    0.33        0.07   
Автомобили                       0.58           0.05    0.70        0.07   
Ремонт и строительство           0.33           0.05    0.21        0.03   
Бытовая техника                  0.23           0.08    0.22        0.07   
mean                             0.51           0.05    0.48        0.06   

                              f1  f1_std  
Мебель и интерьер           0.33    0.05  
Квартиры                    0.82    0.05  
Предложение услуг           0.58    0.04  
Одежда, обувь, аксессуары   0.55    0.03  
Телефоны                    0.52    0.07  
Детская одежда и обувь      0.57    0.03  
Товары для детей и игрушки  0.40    0.07  
Автомобили                  0.63    0.04  
Ремонт и строительство      0.25    0.03  
Бытовая техника             0.22    0.07  
mean                        0.49    0.05

## LDA + KNeighborsClassifier

In [73]:
pipeline_lda_kn = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', LatentDirichletAllocation(50)),
    ('clf', KNeighborsClassifier(n_neighbors=10, metric='cosine'))
])

In [74]:
metrics_lda_kn, errors_lda_kn = eval_table(data['description_norm'], data['category_name'], pipeline_lda_kn)

In [75]:
metrics_lda_kn

precision  precision_std  recall  recall_std  \
Мебель и интерьер                0.35           0.08    0.25        0.16   
Квартиры                         0.74           0.06    0.96        0.02   
Предложение услуг                0.45           0.08    0.40        0.13   
Одежда, обувь, аксессуары        0.49           0.04    0.48        0.06   
Телефоны                         0.60           0.08    0.54        0.09   
Детская одежда и обувь           0.51           0.04    0.61        0.04   
Товары для детей и игрушки       0.58           0.05    0.40        0.07   
Автомобили                       0.61           0.12    0.78        0.05   
Ремонт и строительство           0.28           0.05    0.15        0.06   
Бытовая техника                  0.25           0.11    0.15        0.06   
mean                             0.49           0.07    0.47        0.07   

                              f1  f1_std  
Мебель и интерьер           0.28    0.13  
Квартиры                    0.83    0.04  
Предложение услуг           0.42    0.08  
Одежда, обувь, аксессуары   0.48    0.04  
Телефоны                    0.57    0.06  
Детская одежда и обувь      0.56    0.04  
Товары для детей и игрушки  0.47    0.06  
Автомобили                  0.68    0.09  
Ремонт и строительство      0.19    0.05  
Бытовая техника             0.19    0.07  
mean                        0.47    0.07

_________________________________________________________________________________________________________________________________________________

## SVD + ExtraTreesClassifier

In [77]:
pipeline_svd_et = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=5, max_df=0.4)),
    ('svd', TruncatedSVD(250)),
    ('clf', ExtraTreesClassifier(n_estimators=100, random_state=0))
])

In [78]:
metrics_svd_et, errors_svd_et = eval_table(data['description_norm'], data['category_name'], pipeline_svd_et)

In [79]:
metrics_svd_et

precision  precision_std  recall  recall_std  \
Мебель и интерьер                0.69           0.15    0.14        0.04   
Квартиры                         0.78           0.02    0.86        0.02   
Предложение услуг                0.79           0.05    0.40        0.04   
Одежда, обувь, аксессуары        0.48           0.01    0.71        0.03   
Телефоны                         0.85           0.06    0.38        0.04   
Детская одежда и обувь           0.46           0.01    0.71        0.02   
Товары для детей и игрушки       0.66           0.07    0.23        0.02   
Автомобили                       0.83           0.03    0.59        0.07   
Ремонт и строительство           0.56           0.11    0.11        0.03   
Бытовая техника                  0.54           0.13    0.15        0.07   
mean                             0.66           0.06    0.43        0.04   

                              f1  f1_std  
Мебель и интерьер           0.23    0.07  
Квартиры                    0.82    0.02  
Предложение услуг           0.53    0.05  
Одежда, обувь, аксессуары   0.57    0.02  
Телефоны                    0.53    0.04  
Детская одежда и обувь      0.56    0.01  
Товары для детей и игрушки  0.34    0.03  
Автомобили                  0.69    0.05  
Ремонт и строительство      0.19    0.05  
Бытовая техника             0.23    0.10  
mean                        0.47    0.04

## NMF + ExtraTreesClassifier

In [80]:
pipeline_nmf_et = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('clf', ExtraTreesClassifier(n_estimators=100, random_state=0))
])

In [81]:
metrics_nmf_et, errors_nmf_et = eval_table(data['description_norm'], data['category_name'], pipeline_nmf_et)

In [82]:
metrics_nmf_et

precision  precision_std  recall  recall_std  \
Мебель и интерьер                0.72           0.04    0.57        0.03   
Квартиры                         0.92           0.03    0.96        0.01   
Предложение услуг                0.70           0.03    0.74        0.03   
Одежда, обувь, аксессуары        0.69           0.01    0.79        0.01   
Телефоны                         0.78           0.05    0.78        0.03   
Детская одежда и обувь           0.73           0.01    0.77        0.02   
Товары для детей и игрушки       0.75           0.03    0.60        0.05   
Автомобили                       0.86           0.02    0.90        0.04   
Ремонт и строительство           0.61           0.07    0.46        0.04   
Бытовая техника                  0.68           0.10    0.32        0.02   
mean                             0.74           0.04    0.69        0.03   

                              f1  f1_std  
Мебель и интерьер           0.64    0.03  
Квартиры                    0.94    0.01  
Предложение услуг           0.72    0.02  
Одежда, обувь, аксессуары   0.74    0.01  
Телефоны                    0.78    0.04  
Детская одежда и обувь      0.75    0.01  
Товары для детей и игрушки  0.67    0.03  
Автомобили                  0.88    0.02  
Ремонт и строительство      0.52    0.05  
Бытовая техника             0.43    0.04  
mean                        0.71    0.03

## LDA + ExtraTreesClassifier

In [84]:
pipeline_lda_et = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', LatentDirichletAllocation(50)),
    ('clf', ExtraTreesClassifier(n_estimators=100, random_state=0))
])

In [85]:
metrics_lda_et, errors_lda_et = eval_table(data['description_norm'], data['category_name'], pipeline_lda_et)

In [86]:
metrics_lda_et

precision  precision_std  recall  recall_std  \
Мебель и интерьер                0.44           0.08    0.29        0.07   
Квартиры                         0.79           0.04    0.92        0.03   
Предложение услуг                0.48           0.06    0.51        0.09   
Одежда, обувь, аксессуары        0.52           0.01    0.54        0.02   
Телефоны                         0.58           0.06    0.54        0.09   
Детская одежда и обувь           0.53           0.01    0.60        0.03   
Товары для детей и игрушки       0.48           0.07    0.42        0.08   
Автомобили                       0.65           0.08    0.78        0.04   
Ремонт и строительство           0.39           0.12    0.22        0.08   
Бытовая техника                  0.31           0.08    0.13        0.05   
mean                             0.52           0.06    0.49        0.06   

                              f1  f1_std  
Мебель и интерьер           0.34    0.08  
Квартиры                    0.85    0.03  
Предложение услуг           0.49    0.05  
Одежда, обувь, аксессуары   0.53    0.01  
Телефоны                    0.56    0.07  
Детская одежда и обувь      0.56    0.02  
Товары для детей и игрушки  0.45    0.07  
Автомобили                  0.71    0.05  
Ремонт и строительство      0.27    0.07  
Бытовая техника             0.18    0.06  
mean                        0.49    0.05

## Оценка
Оценим результаты по F1 (средней)

In [96]:
import pandas as pd

In [97]:
df = pd.DataFrame(index=['SVD', 'NMF', 'LDA'], columns=['RF', 'SGD', 'KN', 'ExT'])

In [107]:
df.loc['SVD'] = pd.Series({'RF':metrics_svd_rf['f1'][10], 'SGD':metrics_svd_sgd['f1'][10], 'KN':metrics_svd_kn['f1'][10], 'ExT':metrics_svd_et['f1'][10]})
df.loc['NMF'] = pd.Series({'RF':metrics_nmf_rf['f1'][10], 'SGD':metrics_nmf_sgd['f1'][10], 'KN':metrics_nmf_kn['f1'][10], 'ExT':metrics_nmf_et['f1'][10]})
df.loc['LDA'] = pd.Series({'RF':metrics_lda_rf['f1'][10], 'SGD':metrics_lda_sgd['f1'][10], 'KN':metrics_lda_kn['f1'][10], 'ExT':metrics_lda_et['f1'][10]})


In [122]:
def color(val):
    color = 'blue' if val > 0.7 else 'white'
    return 'color: % s' % color

In [123]:
df.style.applymap(color).format(precision=2, decimal=".")

### Задание № 2 (2 балла)

С помощью gensim постройте 5 тематических моделей с разными параметрами. Как минимум попробуйте: разное количество тем, alpha и eta параметры (в альфа попробуйте "asymmetric" и "auto" помимо 'symmetric' по дефолту, в eta просто попробуйте разные значения), а также разные параметры фильтрации словаря. 

Оцените каждую из моделей с помощью метрик (перплексии и когерентности), а также визуально, просмотрев получаемые темы. Найдите самую хорошую тему для каждой из моделей.

In [125]:
texts = open('wiki_data.txt', encoding='utf-8').read().splitlines()[:5000]
texts = ([normalize(text) for text in texts])

In [126]:
dictinary = gensim.corpora.Dictionary((text.split() for text in texts))

In [127]:
dictinary.filter_extremes(no_above=0.1, no_below=10)
dictinary.compactify()

In [128]:
print(dictinary)

Dictionary<8101 unique tokens: ['1,2', '1,5', '12', '14', '16']...>


In [129]:
corpus = [dictinary.doc2bow(text.split()) for text in texts]

## 1 Модель

In [135]:
lda1 = gensim.models.LdaMulticore(corpus, 
                                 50, # колиество тем
                                 alpha='asymmetric',
                                 id2word=dictinary,
                                 eta=10,
                                 passes=10)

In [134]:
pyLDAvis.enable_notebook()
pyLDAvis.gensim_models.prepare(lda1, corpus, dictinary)

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0      0.114131  0.011103       1        1  59.502595
2      0.043245 -0.046416       2        1  16.525257
1      0.027469  0.028441       3        1  12.446663
3      0.002003 -0.004535       4        1   6.259760
4     -0.003274  0.016920       5        1   3.886068
5     -0.003812  0.002591       6        1   0.843757
6     -0.003802 -0.000169       7        1   0.027004
7     -0.003815 -0.000155       8        1   0.026160
8     -0.003786 -0.000204       9        1   0.023420
9     -0.003809 -0.000117      10        1   0.021963
10    -0.003825 -0.000136      11        1   0.020676
11    -0.003892 -0.000189      12        1   0.019532
12    -0.004005 -0.000192      13        1   0.018508
13    -0.004019 -0.000173      14        1   0.017586
14    -0.004014 -0.000170      15        1   0.016751
15    -0.003992 -0.000183      16        1   0.015992
16    -0.003999 -0.000150      17        1   0.015299
17    -0.004001 -0.000198      18        1   0.014663
26    -0.004127 -0.000155      19        1   0.014180
18    -0.004077 -0.000157      20        1   0.014079
19    -0.004094 -0.000172      21        1   0.013539
20    -0.004019 -0.000150      22        1   0.013038
21    -0.004040 -0.000188      23        1   0.012574
23    -0.004161 -0.000174      24        1   0.012248
22    -0.004167 -0.000200      25        1   0.012141
24    -0.004127 -0.000177      26        1   0.011360
25    -0.004152 -0.000184      27        1   0.011006
27    -0.004182 -0.000199      28        1   0.010360
28    -0.004127 -0.000165      29        1   0.010064
29    -0.004170 -0.000192      30        1   0.009785
30    -0.004129 -0.000183      31        1   0.009521
31    -0.004073 -0.000199      32        1   0.009271
32    -0.004127 -0.000213      33        1   0.009034
33    -0.004180 -0.000195      34        1   0.008809
34    -0.004267 -0.000211      35        1   0.008594
35    -0.004256 -0.000241      36        1   0.008390
36    -0.004212 -0.000203      37        1   0.008195
37    -0.004165 -0.000206      38        1   0.008009
38    -0.004100 -0.000153      39        1   0.007831
39    -0.004113 -0.000201      40        1   0.007661
40    -0.004161 -0.000207      41        1   0.007499
41    -0.004213 -0.000201      42        1   0.007343
42    -0.004094 -0.000199      43        1   0.007193
43    -0.004175 -0.000184      44        1   0.007049
44    -0.004134 -0.000176      45        1   0.006911
45    -0.004182 -0.000183      46        1   0.006779
46    -0.004184 -0.000197      47        1   0.006651
47    -0.004222 -0.000194      48        1   0.006528
48    -0.004151 -0.000216      49        1   0.006409
49    -0.004223 -0.000194      50        1   0.006295, topic_info=             Term        Freq       Total Category  logprob  loglift
1171        армия  935.000000  935.000000  Default  30.0000  30.0000
268           мир  908.000000  908.000000  Default  29.0000  29.0000
851       команда  804.000000  804.000000  Default  28.0000  28.0000
6536  житомирский  742.000000  742.000000  Default  27.0000  27.0000
1681       войско  797.000000  797.000000  Default  26.0000  26.0000
...           ...         ...         ...      ...      ...      ...
1049      система    0.004978  614.306141  Topic50  -8.9780  -2.0501
127    российский    0.004976  564.799613  Topic50  -8.9783  -1.9665
1630     компания    0.004975  653.543694  Topic50  -8.9785  -2.1126
106         фильм    0.004975  578.216307  Topic50  -8.9785  -1.9901
1118        чтобы    0.004974  563.250693  Topic50  -8.9786  -1.9640

[3813 rows x 6 columns], token_table=      Topic      Freq Term
term                      
705       1  0.838661    0
705       2  0.051049    0
705       3  0.051049    0
705       4  0.029171    0
705       5  0.029171    0
...     ...       ...  ...
533       2  0.212484    №
533       3  0.038841    №
533       4  

In [136]:
np.exp2(-lda1.log_perplexity(corpus[:1000]))

472.1753831202855

In [137]:
topics = []
for topic_id, topic in lda1.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

coherence_model_lda1 = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=[text.split() for text in texts], 
                                                   dictionary=dictinary, coherence='c_v')

coherence_model_lda1.get_coherence()

0.3108048824214959

## 2 Модель

In [141]:
lda2 = gensim.models.LdaMulticore(corpus, 
                                 20, # колиество тем
                                 alpha='asymmetric',
                                 id2word=dictinary,
                                 eta=50,
                                 passes=24)

In [142]:
pyLDAvis.gensim_models.prepare(lda2, corpus, dictinary)

PreparedData(topic_coordinates=              x    y  topics  cluster       Freq
topic                                           
0     -0.054140 -0.0       1        1  99.308804
1      0.002836  0.0       2        1   0.086103
2      0.002844 -0.0       3        1   0.065265
3      0.002846 -0.0       4        1   0.064465
4      0.002848 -0.0       5        1   0.056427
5      0.002849 -0.0       6        1   0.048027
6      0.002850 -0.0       7        1   0.040942
7      0.002850  0.0       8        1   0.036675
8      0.002850 -0.0       9        1   0.034483
9      0.002851  0.0      10        1   0.031231
10     0.002851  0.0      11        1   0.029073
11     0.002851  0.0      12        1   0.027194
12     0.002851  0.0      13        1   0.025543
13     0.002851  0.0      14        1   0.024081
14     0.002852  0.0      15        1   0.022777
15     0.002852  0.0      16        1   0.021607
16     0.002852  0.0      17        1   0.020552
17     0.002852  0.0      18        1   0.020105
18     0.002852  0.0      19        1   0.018723
19     0.002852  0.0      20        1   0.017925, topic_info=           Term        Freq       Total Category  logprob  loglift
1171      армия  781.000000  781.000000  Default  30.0000  30.0000
268         мир  760.000000  760.000000  Default  29.0000  29.0000
1037     россия  750.000000  750.000000  Default  28.0000  28.0000
701        уезд  724.000000  724.000000  Default  27.0000  27.0000
116      остров  671.000000  671.000000  Default  26.0000  26.0000
...         ...         ...         ...      ...      ...      ...
1758   подвеска    0.013872  361.302636  Topic20  -8.9994  -1.5409
530     февраль    0.013872  535.808584  Topic20  -8.9994  -1.9349
1493     турнир    0.013872  500.806103  Topic20  -8.9995  -1.8674
1028  результат    0.013872  518.301518  Topic20  -8.9995  -1.9017
92        жизнь    0.013872  486.916225  Topic20  -8.9995  -1.8392

[1470 rows x 6 columns], token_table=      Topic      Freq           Term
term                                
4961      1  0.979631            103
5184      1  0.979628            117
2123      1  0.979623            119
4255      1  0.979619            155
7915      1  0.979630            156
...     ...       ...            ...
1908      1  0.998705          школа
5033      1  0.979630     шокировать
7836      1  0.973956  эквивалентный
1868      1  0.998222           язык
7977      1  0.985249          як-40

[376 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20])

In [143]:
np.exp2(-lda2.log_perplexity(corpus[:1000]))

563.8865034369379

In [144]:
topics = []
for topic_id, topic in lda2.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

coherence_model_lda2 = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=[text.split() for text in texts], 
                                                   dictionary=dictinary, coherence='c_v')

coherence_model_lda2.get_coherence()

0.33357512758842145

## 3 Модель

In [151]:
dictinary3 = gensim.corpora.Dictionary((text.split() for text in texts))
dictinary3.filter_extremes(no_above=0.3, no_below=5)

In [156]:
lda3 = gensim.models.LdaMulticore(corpus, 
                                 30, # колиество тем
                                 alpha='symmetric',
                                 id2word=dictinary3,
                                 eta=1,
                                 passes=5)

In [158]:
pyLDAvis.gensim_models.prepare(lda3, corpus, dictinary3)

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
13    -0.080387 -0.008758       1        1  14.627038
6     -0.103514 -0.063132       2        1  12.534061
19    -0.094041  0.003406       3        1  11.879424
27    -0.067108  0.042258       4        1  11.744771
3     -0.093678  0.086972       5        1  11.484786
25    -0.054446 -0.133614       6        1   8.211068
2     -0.008206  0.041525       7        1   6.403291
0     -0.023608  0.050882       8        1   4.252471
28    -0.016255  0.028533       9        1   2.735729
22    -0.001659 -0.026890      10        1   2.181732
15     0.035975  0.057217      11        1   1.949645
10     0.004267 -0.007998      12        1   1.890568
26     0.044885 -0.040637      13        1   1.451645
14    -0.009573  0.009830      14        1   1.288866
17     0.007119 -0.014370      15        1   1.170427
21     0.034140 -0.008585      16        1   1.091959
29    -0.017125  0.005331      17        1   1.060414
4      0.023644 -0.010223      18        1   0.837605
24    -0.009618  0.010339      19        1   0.828626
9      0.050528 -0.002361      20        1   0.628201
23     0.029248 -0.019005      21        1   0.409683
5      0.028808 -0.024839      22        1   0.376061
12     0.029229  0.007821      23        1   0.333036
1      0.039799  0.003899      24        1   0.143594
20     0.052426 -0.003023      25        1   0.135077
8      0.039185 -0.004457      26        1   0.124876
7      0.038102 -0.000544      27        1   0.087475
18     0.040771  0.007408      28        1   0.055082
11     0.041245  0.009065      29        1   0.041875
16     0.039848  0.003953      30        1   0.040915, topic_info=               Term        Freq       Total Category  logprob  loglift
701           парма  441.000000  441.000000  Default  30.0000  30.0000
2043        венгрия  647.000000  647.000000  Default  29.0000  29.0000
106        соседний  905.000000  905.000000  Default  28.0000  28.0000
3245  ориентировать  377.000000  377.000000  Default  27.0000  27.0000
6536  дружественный  335.000000  335.000000  Default  26.0000  26.0000
...             ...         ...         ...      ...      ...      ...
1407         распад    0.107386  535.052050  Topic30  -7.7782  -0.7123
1118          нация    0.107066  609.423266  Topic30  -7.7812  -0.8454
251       адаптация    0.102102  565.128519  Topic30  -7.8287  -0.8174
2043        венгрия    0.101893  647.727837  Topic30  -7.8307  -0.9559
451         понятно    0.099329  669.896627  Topic30  -7.8562  -1.0150

[1662 rows x 6 columns], token_table=      Topic      Freq Term
term                      
5712      1  0.046081   00
5712      2  0.030721   00
5712      3  0.322566   00
5712      4  0.138243   00
5712      5  0.015360   00
...     ...       ...  ...
686       9  0.032359    №
686      10  0.355954    №
686      13  0.032359    №
686      14  0.032359    №
686      15  0.032359    №

[19014 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[14, 7, 20, 28, 4, 26, 3, 1, 29, 23, 16, 11, 27, 15, 18, 22, 30, 5, 25, 10, 24, 6, 13, 2, 21, 9, 8, 19, 12, 17])

In [159]:
np.exp2(-lda3.log_perplexity(corpus[:1000]))

752.6724200257557

In [160]:
topics = []
for topic_id, topic in lda3.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

coherence_model_lda3 = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=[text.split() for text in texts], 
                                                   dictionary=dictinary, coherence='c_v')

coherence_model_lda3.get_coherence()

0.37559361940053465

## 4 Модель

In [162]:
lda4 = gensim.models.LdaMulticore(corpus, 
                                 17, # колиество тем
                                 alpha='asymmetric',
                                 id2word=dictinary,
                                 eta=0.2,
                                 passes=17)

In [163]:
pyLDAvis.gensim_models.prepare(lda4, corpus, dictinary)

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
12     0.000369  0.124061       1        1  11.579746
9      0.073170 -0.006648       2        1  10.917492
5     -0.109432  0.127173       3        1   8.905373
7     -0.022021  0.014813       4        1   7.901570
1      0.090211 -0.188272       5        1   7.705844
13    -0.028185 -0.021084       6        1   6.639761
0      0.191176  0.070001       7        1   6.541380
10     0.157641  0.057651       8        1   6.043096
16    -0.178636  0.013556       9        1   5.821705
3      0.151811  0.144229      10        1   5.671031
15     0.049476 -0.052358      11        1   4.881897
4     -0.240626  0.100615      12        1   4.303736
6     -0.024814 -0.156554      13        1   4.241041
11    -0.029144 -0.057915      14        1   3.946683
8     -0.075979 -0.175466      15        1   2.103499
2      0.028602 -0.044450      16        1   1.914552
14    -0.033621  0.050647      17        1   0.881594, topic_info=             Term         Freq        Total Category  logprob  loglift
6536  житомирский   862.000000   862.000000  Default  30.0000  30.0000
701          уезд  1092.000000  1092.000000  Default  29.0000  29.0000
69           река   858.000000   858.000000  Default  28.0000  28.0000
1443         матч   821.000000   821.000000  Default  27.0000  27.0000
1440         клуб   847.000000   847.000000  Default  26.0000  26.0000
...           ...          ...          ...      ...      ...      ...
2235       москва    24.141991   621.702502  Topic17  -5.4332   1.4827
1220     польский    17.346998   189.068276  Topic17  -5.7637   2.3425
1124         этап    17.062910   221.588104  Topic17  -5.7802   2.1673
1805      сторона    20.212755   689.897321  Topic17  -5.6108   1.2010
451           дом    16.676088   820.298551  Topic17  -5.8031   0.8355

[1075 rows x 6 columns], token_table=      Topic      Freq Term
term                      
705       3  0.108745    0
705       4  0.027186    0
705       6  0.006797    0
705       7  0.006797    0
705       8  0.652472    0
...     ...       ...  ...
533      12  0.003384    №
533      13  0.223338    №
533      14  0.049067    №
533      15  0.062602    №
533      17  0.005076    №

[7067 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[13, 10, 6, 8, 2, 14, 1, 11, 17, 4, 16, 5, 7, 12, 9, 3, 15])

In [164]:
np.exp2(-lda4.log_perplexity(corpus[:1000]))

406.211005718709

In [165]:
topics = []
for topic_id, topic in lda3.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

coherence_model_lda4 = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=[text.split() for text in texts], 
                                                   dictionary=dictinary, coherence='c_v')

coherence_model_lda4.get_coherence()

0.37559361940053465

## 5 Модель

In [166]:
lda5 = gensim.models.LdaMulticore(corpus, 
                                 30, # колиество тем
                                 alpha='asymmetric',
                                 id2word=dictinary,
                                 eta=333,
                                 passes=3)

In [167]:
pyLDAvis.gensim_models.prepare(lda5, corpus, dictinary)

PreparedData(topic_coordinates=              x    y  topics  cluster       Freq
topic                                           
0     -0.001904  0.0       1        1  98.116442
1     -0.000433 -0.0       2        1   0.392046
2     -0.000188  0.0       3        1   0.157697
4     -0.000027 -0.0       4        1   0.099581
3     -0.000046  0.0       5        1   0.094773
5      0.000025 -0.0       6        1   0.082182
6      0.000021 -0.0       7        1   0.074119
7      0.000054 -0.0       8        1   0.063763
10     0.000089 -0.0       9        1   0.059401
8      0.000055 -0.0      10        1   0.057975
14     0.000118  0.0      11        1   0.050331
9      0.000076 -0.0      12        1   0.050207
11     0.000093 -0.0      13        1   0.050023
15     0.000110 -0.0      14        1   0.048519
16     0.000122  0.0      15        1   0.044858
17     0.000115 -0.0      16        1   0.044798
21     0.000116  0.0      17        1   0.042385
20     0.000116  0.0      18        1   0.041531
23     0.000138 -0.0      19        1   0.041151
19     0.000121  0.0      20        1   0.040913
12     0.000104 -0.0      21        1   0.039954
13     0.000101  0.0      22        1   0.038419
26     0.000120  0.0      23        1   0.037124
24     0.000129 -0.0      24        1   0.035054
18     0.000117  0.0      25        1   0.034060
25     0.000134  0.0      26        1   0.033548
27     0.000133  0.0      27        1   0.033260
28     0.000131  0.0      28        1   0.032406
22     0.000124  0.0      29        1   0.032138
29     0.000135  0.0      30        1   0.031342, topic_info=             Term        Freq       Total Category  logprob  loglift
6536  житомирский  219.000000  219.000000  Default  30.0000  30.0000
701          уезд  211.000000  211.000000  Default  29.0000  29.0000
268           мир  195.000000  195.000000  Default  28.0000  28.0000
3245       летний  189.000000  189.000000  Default  27.0000  27.0000
2043      сборная  187.000000  187.000000  Default  26.0000  26.0000
...           ...         ...         ...      ...      ...      ...
851       команда    0.024899  183.902341  Topic30  -8.9732  -0.8393
116        остров    0.024866  185.493524  Topic30  -8.9746  -0.8493
106         фильм    0.024860  174.811476  Topic30  -8.9748  -0.7902
380         сезон    0.024852  171.244154  Topic30  -8.9751  -0.7699
1329         член    0.024837  151.305528  Topic30  -8.9757  -0.6467

[3695 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
2472      1  0.978353     1100
6027      1  0.975489      128
7572      1  0.977146     1648
7323      1  0.974740     1814
8051      1  0.978585     4000
...     ...       ...      ...
439       1  0.986612     ядро
1868      1  0.989189     язык
4252      1  0.986103     ящик
6055      1  0.977850  ёмкость
87        1  0.989513        …

[656 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 5, 4, 6, 7, 8, 11, 9, 15, 10, 12, 16, 17, 18, 22, 21, 24, 20, 13, 14, 27, 25, 19, 26, 28, 29, 23, 30])

In [168]:
np.exp2(-lda5.log_perplexity(corpus[:1000]))

537.9745571468823

In [169]:
topics = []
for topic_id, topic in lda3.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

coherence_model_lda5 = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=[text.split() for text in texts], 
                                                   dictionary=dictinary, coherence='c_v')

coherence_model_lda5.get_coherence()

0.37559361940053465